# Set up

In [194]:
import duckdb
import pandas as pd
from IPython.display import display
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import warnings
import plotly.express as px
from eda_support_functions import *
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Suppress all warnings
warnings.filterwarnings('ignore')

In [195]:
movie_input = pd.read_csv('/Users/iliasx/Documents/GitHub/box-office-prediction/data/processed_data/movie.csv')
genres = pd.read_csv('/Users/iliasx/Documents/GitHub/box-office-prediction/data/processed_data/genre.csv')
keywords = pd.read_csv('/Users/iliasx/Documents/GitHub/box-office-prediction/data/processed_data/keyword.csv')
production_companies = pd.read_csv('/Users/iliasx/Documents/GitHub/box-office-prediction/data/processed_data/production.csv')

In [196]:
movie = movie_input[['movie_id','imdb_id','year','month','release_date','quarter','original_title',
                     'is_released', 'is_released_US','days_from_us_release',
                     'runtime','revenue_usd_adj','budget_usd_adj','surplus','ratio_adj','roi',
                     'is_first_released_in_cinemas', 'is_first_released_in_cinemas_safe',
                     'release_category','ageCert'
                     ]]

In [197]:
movie.groupby('release_category').size()

release_category
Close streaming release           254
Far streaming release            8238
Not released in major markets    1671
Streaming release                1962
dtype: int64

# Basic Understanding of the Data

In [198]:
movie.head(10)

movie_id    imdb_id  year  month release_date  quarter  \
0    579245  tt8655470  2019     10   2019-10-23        4   
1     14347  tt0086973  1984      2   1984-02-17        1   
2    340666  tt4550098  2016     11   2016-11-04        4   
3     14351  tt0473024  2006      9   2006-09-01        3   
4    208869  tt2556874  2014      4   2014-04-30        2   
5     14353  tt0963194  2008     11   2008-11-07        4   
6    276496  tt2192016  2014      7   2014-07-17        3   
7     14359  tt0918927  2008      2   2008-02-27        1   
8    340674  tt1901024  2016     10   2016-10-12        4   
9     54986  tt0245837  2000      1   2000-01-29        1   

            original_title  is_released  is_released_US  days_from_us_release  \
0              Hors Normes         True           False                  -1.0   
1          Blame It on Rio         True            True               24060.0   
2        Nocturnal Animals         True            True                  74.0   
3                Crossover         True            True               15828.0   
4                  Plastic         True            True                 248.0   
5  Repo! The Genetic Opera        False           False                  -1.0   
6           The Dark Horse         True            True               12670.0   
7                    Doubt         True           False                  -1.0   
8              Dark Crimes        False           False                  -1.0   
9                      춘향뎐         True            True               17952.0   

   runtime  revenue_usd_adj  budget_usd_adj       surplus  ratio_adj  \
0      114     2.310696e+07    1.525554e+07 -3.702062e+06   1.514660   
1      100     5.467794e+07    2.639382e+07  9.451481e+05   2.071619   
2      117     3.848256e+07    2.856498e+07 -9.323700e+06   1.347194   
3       95     1.059454e+07    8.766228e+06 -3.468957e+06   1.208563   
4      102     1.253615e+06    9.345891e+06 -8.719083e+06   0.134135   
5       98     2.662405e+05    1.202941e+07 -1.189628e+07   0.022132   
6      124     2.396720e+06    2.702902e+06 -1.504542e+06   0.886721   
7      104     7.316706e+07    2.830448e+07  8.279050e+06   2.584999   
8       93     2.693487e+04    5.688104e+06 -5.674636e+06   0.004735   
9      137     1.413762e+06    4.423664e+06 -3.716783e+06   0.319591   

        roi  is_first_released_in_cinemas  is_first_released_in_cinemas_safe  \
0 -0.242670                         False                              False   
1  0.035809                          True                               True   
2 -0.326403                          True                               True   
3 -0.395718                          True                               True   
4 -0.932932                          True                               True   
5 -0.988934                         False                              False   
6 -0.556640                          True                               True   
7  0.292500                         False                              False   
8 -0.997632                         False                              False   
9 -0.840205                          True                               True   

                release_category ageCert  
0              Streaming release       U  
1          Far streaming release       R  
2          Far streaming release       R  
3          Far streaming release    PG13  
4          Far streaming release       R  
5  Not released in major markets       U  
6          Far streaming release       U  
7              Streaming release       U  
8  Not released in major markets       U  
9          Far streaming release       U

In [199]:
null_percentage_all = movie.isnull().mean() * 100

zero_percentage_all = (movie == 0).mean() * 100

null_zero_percentage_all = pd.DataFrame({'Null Percentage': null_percentage_all, 'Zero Percentage': zero_percentage_all})
print(null_zero_percentage_all)

                                   Null Percentage  Zero Percentage
movie_id                                  0.000000         0.000000
imdb_id                                   0.024742         0.000000
year                                      0.000000         0.000000
month                                     0.000000         0.000000
release_date                              0.000000         0.000000
quarter                                   0.000000         0.000000
original_title                            0.000000         0.000000
is_released                               0.000000        13.781443
is_released_US                            0.000000        27.983505
days_from_us_release                      0.000000         0.321649
runtime                                   0.000000         0.000000
revenue_usd_adj                           0.000000         0.000000
budget_usd_adj                            0.000000         0.000000
surplus                                   0.0000

In [200]:
movie[movie.budget_usd_adj != 0 ][['revenue_usd_adj','budget_usd_adj','surplus','ratio_adj','roi']].describe(percentiles=[0.01, 0.05, 0.1, 0.25, 0.50, 0.75, 0.9, 0.95, 0.99, 0.999, 0.9999]).drop('count').style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
})

In [201]:
print('Smallest ratio movies')
display(movie.sort_values(by='ratio_adj').head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))

print('Biggest ratio movies')
display(movie[movie.budget_usd_adj != 0 ].sort_values(by='ratio_adj', ascending=False).head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))


Smallest ratio movies


Biggest ratio movies


In [202]:
print('Movies with ratio_adj > more than 10 and less than 0.1')
display(movie[(movie.ratio_adj > 10) | (movie.ratio_adj < 0.1)][['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'ratio_adj']])


Movies with ratio_adj > more than 10 and less than 0.1


movie_id             original_title  revenue_usd_adj  budget_usd_adj  \
5         14353    Repo! The Genetic Opera     2.662405e+05    1.202941e+07   
8        340674                Dark Crimes     2.693487e+04    5.688104e+06   
20       208958            One Night Stand     3.018308e+05    3.773626e+06   
23       471105               Armomurhaaja     1.498400e+04    4.350755e+05   
24        33613  Luftslottet som sprängdes     6.288467e+07    5.681109e+06   
...         ...                        ...              ...             ...   
12114    470878         I Can Only Imagine     1.044608e+08    8.494044e+06   
12118    276478           The Kitchen Toto     2.622214e+05    8.567825e+06   
12119     33557             Daddy and Them     1.155837e+04    6.882033e+06   
12120     14337                     Primer     8.798065e+05    1.129123e+04   
12122     54948        Uma Vida em Segredo     6.225913e+04    1.032305e+06   

       ratio_adj  
5       0.022132  
8       0.004735  
20      0.079984  
23      0.034440  
24     11.069084  
...          ...  
12114  12.298126  
12118   0.030605  
12119   0.001680  
12120  77.919429  
12122   0.060311  

[2424 rows x 5 columns]

Example of outlier, indeed a wrong imdb data entry

https://www.imdb.com/title/tt1334328/


movie_id	original_title	revenue_usd_adj	budget_usd_adj	ratio_adj

53128	Ψυχή Βαθιά	2.903065e+06	4.092371	7.093847e+0

In [203]:
print('Smallest ROI movies')
display(movie.sort_values(by='roi').head(15)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))

print('Biggest ROI movies')
display(movie[movie.budget_usd_adj != 0 ].sort_values(by='roi', ascending=False).head(15)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))


Smallest ROI movies


Biggest ROI movies


In [204]:
print('Smallest Surplus movies')
display(movie.sort_values(by='surplus').head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))

print('Biggest Surplus movies')
display(movie[movie.budget_usd_adj != 0 ].sort_values(by='surplus', ascending=False).head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))


Smallest Surplus movies


Biggest Surplus movies


In [205]:
print('Basic statistics per is_released_US flag for the ratio and the ROI: ')
display(movie.groupby('is_released_US')[['ratio_adj', 'roi']].describe().style.format("{:,.2f}"))

Basic statistics per is_released_US flag for the ratio and the ROI: 


In [206]:
print('Basic statistics per release_category for the ratio:')
display(movie.groupby('release_category')[['ratio_adj']].describe().style.format("{:,.2f}"))

Basic statistics per release_category for the ratio:


In [207]:
print('Basic statistics per release_category for the ROI:')
display(movie.groupby('release_category')[['roi']].describe().style.format("{:,.2f}"))

Basic statistics per release_category for the ROI:


In [208]:
print('Basic statistics per release_category for the ratio and the ROI: ')
display(movie.groupby(['release_category'])[['ratio_adj', 'roi']].describe().style.format("{:,.2f}"))

Basic statistics per release_category for the ratio and the ROI: 


In [209]:
movie[movie.original_title == 'The Irishman']

movie_id    imdb_id  year  month release_date  quarter original_title  \
7968    398978  tt1302006  2019     11   2019-11-01        4   The Irishman   
8937    255839  tt0077749  1978      2   1978-02-28        1   The Irishman   

      is_released  is_released_US  days_from_us_release  runtime  \
7968        False           False                  -1.0      209   
8937         True            True               26240.0      108   

      revenue_usd_adj  budget_usd_adj       surplus  ratio_adj       roi  \
7968     1.154717e+06    1.895024e+08 -1.889251e+08   0.006093 -0.996953   
8937     3.303580e+06    4.461426e+06 -2.809636e+06   0.740476 -0.629762   

      is_first_released_in_cinemas  is_first_released_in_cinemas_safe  \
7968                         False                              False   
8937                          True                               True   

                   release_category ageCert  
7968  Not released in major markets       U  
8937          Far streaming release       U

In [210]:
filtered_data = movie

In [211]:

fig = px.scatter(filtered_data, x='budget_usd_adj', y='revenue_usd_adj',
                 color='release_category', 
                 labels={'budget_usd_adj': 'Adjusted Budget (USD)', 'revenue_usd_adj': 'Adjusted Revenue (USD)'},
                 title='Scatter Plot of Revenue vs Budget by Release Category',
                 log_x=True, log_y=True, 
                 color_discrete_sequence=px.colors.qualitative.Pastel)

fig.update_layout(xaxis_title='Adjusted Budget (USD)',
                  yaxis_title='Adjusted Revenue (USD)',
                  legend_title='Release Category',
                  xaxis_tickangle=-45,
                  xaxis_tickfont_size=12,
                  yaxis_tickfont_size=12)

fig.show()

In [212]:
fig = px.box(filtered_data, x='release_category', y='roi', 
             title='Boxplot of ROI by Release Category (Log Scale)',
             labels={'roi': 'ROI', 'release_category': 'Release Category'},
             log_y=True,
             color='release_category',
             color_discrete_map= {
                'Streaming release': 'rgba(204, 80, 62, 1)',
                'Not released in major markets': 'rgba(237, 172, 8, 1)',
                'Far streaming release': 'rgba(115, 175, 72, 1)',
                'Close streaming release': 'rgba(95, 70, 144, 1)'
             }
             )

fig.update_layout(
    plot_bgcolor='white',
    paper_bgcolor='white',
    yaxis=dict(gridcolor='lightgray', zerolinecolor='lightgray'),
    xaxis=dict(gridcolor='lightgray', zerolinecolor='lightgray'),
    font=dict(size=12),
    legend_title_text='Release Category',
    
)

fig.show()

# Outliers

In [213]:
#movie = movie[movie['release_category'] != 'Not released in major markets']

In [214]:
# Determining outliers for specific columns and appending the information to the dataset

# Selecting the specific columns for outlier analysis
specific_columns = ['revenue_usd_adj', 'budget_usd_adj', 'surplus', 'ratio_adj','roi']

# Calculating IQR for the specific columns
Q1_specific = movie[specific_columns].quantile(0.25)
Q3_specific = movie[specific_columns].quantile(0.75)

Q1_specific_log = np.log(movie[specific_columns]).quantile(0.25)
Q3_specific_log = np.log(movie[specific_columns]).quantile(0.75)

IQR_specific = Q3_specific - Q1_specific
IQR_specific_log = Q3_specific_log - Q1_specific_log

# Creating outlier flags for each specific column
for column in specific_columns:
    lower_bound = Q1_specific[column] - 1.5 * IQR_specific[column]
    upper_bound = Q3_specific[column] + 1.5 * IQR_specific[column]
    lower_bound_log = Q1_specific_log[column] - 0.75 * IQR_specific_log[column]
    upper_bound_log = Q3_specific_log[column] + 0.75 * IQR_specific_log[column]
    movie[f'{column}_outlier'] = ((movie[column] < lower_bound) | (movie[column] > upper_bound))
    movie[f'{column}_outlier_log'] = ((np.log(movie[column]) < lower_bound_log) | (np.log(movie[column]) > upper_bound_log))

In [215]:
# showing the outliers
outliers = movie[movie['roi_outlier']]

In [216]:
movie

movie_id    imdb_id  year  month release_date  quarter  \
0        579245  tt8655470  2019     10   2019-10-23        4   
1         14347  tt0086973  1984      2   1984-02-17        1   
2        340666  tt4550098  2016     11   2016-11-04        4   
3         14351  tt0473024  2006      9   2006-09-01        3   
4        208869  tt2556874  2014      4   2014-04-30        2   
...         ...        ...   ...    ...          ...      ...   
12120     14337  tt0390384  2004     10   2004-10-08        4   
12121    295699  tt2937696  2016      3   2016-03-30        1   
12122     54948  tt0327206  2001      5   2001-05-26        2   
12123     14342  tt0119053  1998      5   1998-05-29        2   
12124     54952  tt0492869  2007      2   2007-02-09        1   

               original_title  is_released  is_released_US  \
0                 Hors Normes         True           False   
1             Blame It on Rio         True            True   
2           Nocturnal Animals         True            True   
3                   Crossover         True            True   
4                     Plastic         True            True   
...                       ...          ...             ...   
12120                  Primer         True           False   
12121  Everybody Wants Some!!         True            True   
12122     Uma Vida em Segredo        False           False   
12123           Almost Heroes         True            True   
12124                 Antônia        False           False   

       days_from_us_release  ...  revenue_usd_adj_outlier  \
0                      -1.0  ...                    False   
1                   24060.0  ...                    False   
2                      74.0  ...                    False   
3                   15828.0  ...                    False   
4                     248.0  ...                    False   
...                     ...  ...                      ...   
12120                  -1.0  ...                    False   
12121                 211.0  ...                    False   
12122                  -1.0  ...                    False   
12123               18845.0  ...                    False   
12124                  -1.0  ...                    False   

       revenue_usd_adj_outlier_log  budget_usd_adj_outlier  \
0                            False                   False   
1                            False                   False   
2                            False                   False   
3                            False                   False   
4                            False                   False   
...                            ...                     ...   
12120                        False                   False   
12121                        False                   False   
12122                         True                   False   
12123                        False                   False   
12124                        False                   False   

       budget_usd_adj_outlier_log  surplus_outlier  surplus_outlier_log  \
0                           False            False                False   
1                           False            False                False   
2                           False            False                False   
3                           False            False                False   
4                           False            False                False   
...                           ...              ...                  ...   
12120                        True            False                False   
12121                       False            False                False   
12122                        True            False                False   
12123                       False             True                False   
12124                        True            False                False   

       ratio_adj_outlier  ratio_adj_outlier_log roi_outlier roi_outlier_log  
0                  False

In [217]:
outlier_features = ['revenue_usd_adj_outlier', 'revenue_usd_adj_outlier_log',
                    'budget_usd_adj_outlier', 'budget_usd_adj_outlier_log',
                    'surplus_outlier', 'surplus_outlier_log',
                    'ratio_adj_outlier', 'ratio_adj_outlier_log',
                    'roi_outlier', 'roi_outlier_log']
# Create subplots
fig = make_subplots(rows=5, cols=2, subplot_titles=outlier_features)

# Adding scatter plots to the respective subplot
for i, feature in enumerate(outlier_features):
    row = i // 2 + 1
    col = i % 2 + 1
    filtered_data = movie[movie[feature]]  # Filter data for outliers
    fig.add_trace(
        go.Scattergl(x=filtered_data['budget_usd_adj'], y=filtered_data['revenue_usd_adj'],
                     mode='markers', name=feature,
                     marker=dict(size=7, opacity=0.7)),
        row=row, col=col
    )

# Update axes and layout
fig.update_xaxes(type='log', title_text='Budget (USD)')
fig.update_yaxes(type='log', title_text='Revenue (USD)')
fig.update_layout(height=1500, width=1000, title_text="Scatter plots for Outliers by Category", showlegend=False)

# Show plot
fig.show()

In [218]:
outlier_features = ['revenue_usd_adj_outlier', 'revenue_usd_adj_outlier_log',
                    'budget_usd_adj_outlier', 'budget_usd_adj_outlier_log',
                    'surplus_outlier', 'surplus_outlier_log',
                    'ratio_adj_outlier', 'ratio_adj_outlier_log',
                    'roi_outlier', 'roi_outlier_log']

# Create a 5x2 subplot grid
fig = make_subplots(rows=5, cols=2, subplot_titles=outlier_features)

# Populate the subplots with scatter plots
for index, feature in enumerate(outlier_features):
    row = (index // 2) + 1
    col = (index % 2) + 1
    # Filter data for the current feature
    current_data = movie[movie[feature]]

    # Add a scatter plot to the current subplot
    fig.add_trace(
        go.Scattergl(
            x=current_data['budget_usd_adj'],
            y=current_data['revenue_usd_adj'],
            mode='markers',
            marker=dict(size=7, opacity=0.7),
            name=f'Outliers in {feature}'  # Legend name
        ),
        row=row,
        col=col
    )

    # Print number of outliers in the console/log
    print(f'Number of outliers in {feature}: ', len(current_data))

# Update layout for better appearance and readability
fig.update_layout(height=1500, width=1200, title_text="Scatter plots of Various Outlier Features", showlegend=True)
fig.update_xaxes(title_text='Budget (USD, log scale)', type='log')
fig.update_yaxes(title_text='Revenue (USD, log scale)', type='log')

# Show the figure
fig.show()


Number of outliers in revenue_usd_adj_outlier:  1507
Number of outliers in revenue_usd_adj_outlier_log:  1288
Number of outliers in budget_usd_adj_outlier:  1027
Number of outliers in budget_usd_adj_outlier_log:  1181
Number of outliers in surplus_outlier:  2305
Number of outliers in surplus_outlier_log:  364
Number of outliers in ratio_adj_outlier:  1141
Number of outliers in ratio_adj_outlier_log:  1697
Number of outliers in roi_outlier:  1141
Number of outliers in roi_outlier_log:  576


In [219]:
movie[(movie['release_category'] == 'Far streaming release')][[
    'revenue_usd_adj', 'budget_usd_adj', 'surplus', 'ratio_adj', 'roi'
]].describe().drop('count').style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
})

In [220]:
movie[(movie['release_category'] != 'Far streaming release')][[
    'revenue_usd_adj', 'budget_usd_adj', 'surplus', 'ratio_adj', 'roi'
]].describe().drop('count').style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
})

In [221]:
movie_no_out = movie[(movie['release_category'] == 'Far streaming release')]

fig = px.scatter(movie_no_out, x='budget_usd_adj', y='revenue_usd_adj',
                    labels={'budget_usd_adj': 'Adjusted Budget (USD)', 'revenue_usd_adj': 'Adjusted Revenue (USD)'},
                    title='Scatter Plot of Revenue vs Budget for Movies within Scope with Far Streaming Release',
                    hover_name='original_title',
                    log_x=True, log_y=True)

fig.update_layout(xaxis_title='Adjusted Budget (USD)',
                    yaxis_title='Adjusted Revenue (USD)',
                    xaxis_tickangle=-45,
                    xaxis_tickfont_size=12,
                    yaxis_tickfont_size=12,
                    height=800,
                    width=800)

fig.show()


In [222]:
print('Smallest ratio movies')
display(movie_no_out.sort_values(by='ratio_adj').head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.5f}"
}))

print('Biggest ratio movies')
display(movie_no_out.sort_values(by='ratio_adj', ascending=False).head(10)[['movie_id', 'original_title', 'revenue_usd_adj','budget_usd_adj', 'surplus', 'ratio_adj','roi']].style.format({
    'revenue_usd_adj': "${:,.0f}",
    'budget_usd_adj': "${:,.0f}",
    'surplus': "${:,.0f}",
    'ratio_adj': "{:.2f}",
    'roi': "{:.2f}"
}))


Smallest ratio movies


Biggest ratio movies


# Genres

In [223]:
# Join the movie and the genre table
movie_genre = movie.merge(genres, how='left', on='movie_id')

In [224]:
# Lets do some EDA on the genres
# How many genres are there?
print('Number of genres: ', len(movie_genre['name'].unique()))
# How many movies are there in each genre?
print('Number of movies in each genre: ')
print(movie_genre['name'].value_counts())
# How many movies charecterized by more than one genre?



Number of genres:  20
Number of movies in each genre: 
name
drama              6450
comedy             4479
thriller           2839
action             2612
romance            2470
crime              1875
adventure          1380
horror             1281
science_fiction     959
mystery             880
fantasy             820
family              699
history             604
war                 435
music               375
documentary         173
western             146
animation           124
tv_movie              7
Name: count, dtype: int64


In [225]:
# Number genres per movie
print('Number of genres per movie: {0:.2f}'.format(movie_genre.groupby('movie_id')['name'].count().mean()))

Number of genres per movie: 2.36


In [226]:
# Can you give some basic statistics per genre for the ratio and the ROI?
print('Basic statistics per genre for the ratio and the ROI: ')
display(movie_genre.groupby('name')[['ratio_adj', 'roi']].describe().style.format("{:,.2f}"))


Basic statistics per genre for the ratio and the ROI: 


In [227]:
# Can you give some basic statistics per genre for the ratio and the ROI?
print('Basic statistics per US theatrical release for the ratio and the ROI: ')
display(movie_genre.groupby('name')[['ratio_adj', 'roi']].describe().style.format("{:,.2f}"))

Basic statistics per US theatrical release for the ratio and the ROI: 


# Production Companies

In [228]:
# Join the movie and the production companies table
movie_production_companies = movie.merge(production_companies, how='left', on='movie_id')

In [229]:
# Number of production companies
print('Number of production companies: ', len(movie_production_companies['company_name'].unique()))
# # Number of parent companies (companies that own other companies)
# print('Number of parent companies: ', len(movie_production_companies['parent_name'].unique()))

Number of production companies:  11728


In [230]:
# Number of production companies per movie
print('Number of production companies per movie: {0:.2f}'.format(movie_production_companies.groupby('movie_id')['company_name'].count().mean()))

Number of production companies per movie: 3.08


In [231]:
# Biggest production companies (by number of movies and by revenue)
biggest_companies = movie_production_companies.groupby('company_name').agg({'movie_id': 'count', 'revenue_usd_adj': 'sum'})
biggest_companies.columns = ['Number of Movies', 'Total Revenue']
biggest_companies = biggest_companies.sort_values(by='Number of Movies', ascending=False).head(10)
display(biggest_companies)

Number of Movies  Total Revenue
company_name                                         
warner_bros_pictures               642   1.182536e+11
universal_pictures                 619   1.092464e+11
columbia_pictures                  494   8.090397e+10
paramount_pictures                 475   9.363414e+10
20th_century_fox                   462   9.152053e+10
canal_                             341   1.073558e+10
new_line_cinema                    253   3.938166e+10
metro_goldwyn_mayer                239   2.607072e+10
france_2_cinema                    222   3.403914e+09
touchstone_pictures                195   2.625546e+10

In [232]:
# # Biggest parent production companies (by number of movies and by revenue)
# biggest_parent_companies = movie_production_companies.groupby('parent_name').agg({'movie_id': 'count', 'revenue_usd_adj': 'sum'})
# biggest_parent_companies.columns = ['Number of Movies', 'Total Revenue']
# biggest_parent_companies = biggest_parent_companies.sort_values(by='Number of Movies', ascending=False).head(10).format({
#     'Total Revenue': "${:,.0f}"
# })
# display(biggest_parent_companies)

In [233]:
# # Companies with the most subsidiaries
# subsidiaries = movie_production_companies.groupby('parent_name').agg({'company_name': 'nunique'})
# subsidiaries.columns = ['Number of Subsidiaries']
# subsidiaries = subsidiaries.sort_values(by='Number of Subsidiaries', ascending=False).head(10)
# display(subsidiaries)

# Keywords

In [234]:
movie_keywords = movie.merge(keywords, how='left', on='movie_id')

In [235]:
print('Number of keywords: ', len(movie_keywords['keyword_name'].unique()))

Number of keywords:  15632


In [236]:
# On average, how many keywords are there per movie?
print('Average number of keywords per movie: ', movie_keywords.groupby('movie_id')['keyword_name'].count().mean())

Average number of keywords per movie:  7.4450309278350515


In [237]:
# The most popular keywords (by number of movies and by revenue)
popular_keywords = movie_keywords.groupby('keyword_name').agg({'movie_id': 'count', 'revenue_usd_adj': 'sum'})
popular_keywords.columns = ['Number of Movies', 'Total Revenue']
popular_keywords = popular_keywords.sort_values(by='Number of Movies', ascending=False).head(10).style.format({
    'Total Revenue': "${:,.0f}"
})
display(popular_keywords)

# Time analysis

In [238]:
plot_and_export_categorical_distribution(movie, 'runtime', 0, False, True, "charts", True)

In [239]:
plot_and_export_categorical_distribution(movie, 'year', 0, False, True, "charts", True)

In [240]:
plot_and_export_categorical_distribution(movie, 'quarter', 0, False, True, "charts", True)

In [241]:
plot_and_export_categorical_distribution(movie, 'month', 0, False, True, "charts", True)

In [242]:
plot_and_export_categorical_distribution(movie, 'ageCert', 0, False, True, "charts", True)